## Check with some actual inputs

In [127]:
import re
import pandas as pd
from pyabsa import AspectPolarityClassification as APC

def highlight_focuswords(string,lexicon):
    outputs = []
    for term in lexicon:
        for match in re.finditer(term,string):
            outputs.append(string[:match.start()] + '[ASP]' + term + '[ASP]' + string[match.end():])
    return outputs

lexicon = ['reane']
string = 'reane is een reane'

highlight_focuswords(string,lexicon)

['[ASP]reane[ASP] is een reane', 'reane is een [ASP]reane[ASP]']

In [208]:
lexicon = pd.read_csv('EPA_Lexicon')
lexicon = lexicon['Lexicon'].to_list()

df = pd.read_parquet('Climate_Labels_Dataset.parquet')
df = df[(df['Final_Climate_Change_Level_Label']=='High') | (df['Final_Climate_Change_Level_Label']=='Medium')].reset_index(drop=True)
df = df.drop(['Sentiment_Label', 'Sentiment_Label_R', 'Level_Climate_Change_Topic', 'Level_Climate_Change_Topic_R', 'was_I_retarded?'], axis=1)

samples = []
sample_article_index = []
for i,article in enumerate(df['Text']):
    new_samples = highlight_focuswords(article,lexicon)
    sample_article_index.extend([i]*len(new_samples))
    samples.extend(new_samples)

# print(samples[23])

In [163]:
classifier = APC.SentimentClassifier('english',
                                     auto_device=True,  # False means load model on CPU
                                     cal_perplexity=True,
                                     )


[2023-05-18 15:21:50] (2.3.1) Downloading checkpoint:english 
[2023-05-18 15:21:50] (2.3.1) Notice: The pretrained model are used for testing, it is recommended to train the model on your own custom datasets
[2023-05-18 15:21:50] (2.3.1) Checkpoint already downloaded, skip
FindFile Warning --> multiple targets ['checkpoints\\APC_ENGLISH_CHECKPOINT\\fast_lcf_bert_English_acc_84.65_f1_82.39\\fast_lcf_bert.config', 'checkpoints\\ATEPC_ENGLISH_CHECKPOINT\\fast_lcf_atepc_English_cdw_apcacc_82.36_apcf1_81.89_atef1_75.43\\fast_lcf_atepc.config'] found, only return the shortest path: <checkpoints\APC_ENGLISH_CHECKPOINT\fast_lcf_bert_English_acc_84.65_f1_82.39\fast_lcf_bert.config>
FindFile Warning --> multiple targets ['checkpoints\\APC_ENGLISH_CHECKPOINT\\fast_lcf_bert_English_acc_84.65_f1_82.39\\fast_lcf_bert.config', 'checkpoints\\ATEPC_ENGLISH_CHECKPOINT\\fast_lcf_atepc_English_cdw_apcacc_82.36_apcf1_81.89_atef1_75.43\\fast_lcf_atepc.config'] found, only return the shortest path: <checkpoi

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
c:\ProgramData\Anaconda3\envs\pyabsa\lib\site-packages\transformers\convert_slow_tokenizer.py:454: UserWarning: The sentencepiece tokenizer that you are converting to a fast tokenizer uses the byte fallback option which is not implemented in the fast tokenizers. In practice this means that the fast version of the tokenizer can produce unknown tokens whereas the sentencepiece version would have converted these unknown tokens into a sequence of byte tokens matching the original piece of text.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Some weights of the model checkpoint at microsoft/deberta-v3-base were not used when initializing DebertaV2Model: ['lm_predictions.lm_head.bias', 'mask_predictions.LayerNorm.bias', 'mask_predictions.dense.bias', 'lm_predictions.lm_head.dense.bias', 'm

In [168]:
print(classifier.config)

{'model': <class 'pyabsa.tasks.AspectPolarityClassification.models.__lcf__.fast_lcf_bert.FAST_LCF_BERT'>, 'optimizer': 'adamw', 'learning_rate': 1e-05, 'cache_dataset': False, 'warmup_step': -1, 'deep_ensemble': False, 'use_bert_spc': True, 'max_seq_len': 80, 'patience': 5, 'SRD': 3, 'dlcf_a': 2, 'dca_p': 1, 'dca_layer': 3, 'use_syntax_based_SRD': False, 'sigma': 0.3, 'lcf': 'cdw', 'lsa': True, 'window': 'lr', 'eta': -1, 'eta_lr': 0.001, 'dropout': 0.5, 'l2reg': 1e-08, 'num_epoch': 30, 'batch_size': 16, 'initializer': 'xavier_uniform_', 'seed': 6311, 'output_dim': 3, 'log_step': 2234, 'dynamic_truncate': True, 'srd_alignment': True, 'evaluate_begin': 0, 'similarity_threshold': 1, 'cross_validate_fold': -1, 'use_amp': True, 'overwrite_cache': False, 'pretrained_bert': 'microsoft/deberta-v3-base', 'use_torch_compile': False, 'dataset': ['113.Laptop14', '114.Restaurant14', '116.Restaurant16', '101.ACL_Twitter', '109.MAMS', '117.Television', '118.TShirt', '119.Yelp', '121.MOOC_En', '129.Ka

In [175]:
# instance inference
apc_result = classifier.predict(samples
,
                #    save_result=True,
                   print_result=True,  # print the result
                   ignore_error=True,  # ignore the error when the model cannot predict the input
                   )

len(apc_result)

[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-18 15:45:23] (2.3.1) [ASP] tag is detected, please use [B-ASP] and [E-ASP] to annotate aspect terms.
[2023-05-1

run inference: 100%|██████████| 44/44 [18:24<00:00, 25.10s/it]


[2023-05-18 16:04:02] (2.3.1) Example 0: <anthropogenic:Negative(confidence:0.654, ref:-100)> climate change before the world’s experts and before the science itself had matured, and then withheld it from the broader scientific community.” McCarron said the company openly shared findings in peer-reviewed publications and actively contributed to the work of the United Nation’s Intergovernmental Panel on Climate Change.
“The allegations repeated today are an attempt to limit free speech and are the antithesis of scientific inquiry,” McCarron said. “Left unchallenged, they could stifle the search for solutions to the real risks from climate change.”
Advertisement
While ExxonMobil might have been the company publicly in the crosshairs this week, the carefully coordinated announcement in New York could signal the beginning stages of a broader reckoning for big energy companies facing questions about what they knew about climate change, and when.
At least Gore seemed to think so.
Years from 

1309

In [211]:
from sklearn.metrics import precision_score, accuracy_score

def categorize_score(score, negative_threshold, positive_threshold):
  if score < negative_threshold:
      return -1
  elif score > positive_threshold:
      return 1
  else:
      return 0
  
def sent_crosstab(df, truth, guess):
    # create a crosstab of the two labels
    crosstab = pd.crosstab(df[truth], df[guess])

    print(crosstab)
    # calculate precision and accuracy for each value
    for col in crosstab.columns:
        precision = precision_score(df[truth], df[guess], labels=[col], average='macro')
        accuracy = accuracy_score(df[truth], df[guess])
        print(f"Precision for {col}: {precision}")
        print(f"Accuracy for {col}: {accuracy}")

In [218]:
from statistics import mean
df_result = pd.DataFrame(apc_result,columns=apc_result[0])
df_result = df_result.explode(['aspect', 'sentiment', 'confidence'], ignore_index=True)
df_result['article_index'] = sample_article_index
df_result
# Map sentiment values to numerical values
sentiment_mapping = {"Positive": 1, "Negative": -1, "Neutral": 0}

df_result=df_result.groupby('article_index').agg({'sentiment': lambda x: list(x), 'confidence': lambda x: list(x)})

# Convert sentiment values to numeric and multiply with confidence values
df_result['final_sentiment'] = df_result.apply(lambda row: mean([sentiment_mapping[s] * c for s, c in zip(row['sentiment'], row['confidence'])]), axis=1)
df_result['final_sentiment'] = df_result['final_sentiment'].apply(lambda x: categorize_score(x, 0, 0))
df_result['final_sentiment'].value_counts()
df['sentiment_pyabsa'] = df_result['final_sentiment']
sent_crosstab(df, 'Final_Sentiment_Label', 'sentiment_pyabsa')



sentiment_pyabsa       -1   0   1
Final_Sentiment_Label            
-1                     47   5  17
 0                      6   1   3
 1                      9   2  10
Precision for -1: 0.7580645161290323
Accuracy for -1: 0.58
Precision for 0: 0.125
Accuracy for 0: 0.58
Precision for 1: 0.3333333333333333
Accuracy for 1: 0.58


sentiment_pyabsa       -1   0   1
Final_Sentiment_Label            
-1                     46   7  16
 0                      6   1   3
 1                      9   3   9
Precision for -1: 0.7540983606557377
Accuracy for -1: 0.56
Precision for 0: 0.09090909090909091
Accuracy for 0: 0.56
Precision for 1: 0.32142857142857145
Accuracy for 1: 0.56
